#### Include steps
###### - Load data
###### - Explorative data analysis
###### - Pre-processing and normalization 
###### - Save data

In [0]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns
from collections import OrderedDict
from functools import reduce
import warnings
warnings.filterwarnings("ignore")

In [0]:
customers = pd.read_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/olist_customers_dataset.csv')
order_items = pd.read_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/olist_order_items_dataset.csv')
order_payments = pd.read_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/olist_order_payments_dataset.csv')
order_reviews = pd.read_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/olist_order_reviews_dataset.csv')
orders = pd.read_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/olist_orders_dataset.csv')
product = pd.read_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/olist_products_dataset.csv')
sellers = pd.read_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/olist_sellers_dataset.csv')
product_name = pd.read_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/product_category_name_translation.csv')

In [0]:
# displaying data shape
dataset = {
    'customers': customers,
    'order_items': order_items,
    'order_payments': order_payments,
    'orders': orders,
    'order_reviews':order_reviews,
    'product': product,
    'product_name': product_name,
    'sellers': sellers
}

for x, y in dataset.items():
    print(f'{x}')
    print(y.info())
    print('Missing data:', y.isnull().any().any())
    if y.isnull().any().any():
      print("No. missing value: ")
      print(f'{y.isnull().sum()}\n')
    print("--------------------------------------------------------------")

customers
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99441 entries, 0 to 99440
Data columns (total 3 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 customer_id 99441 non-null object
 1 customer_unique_id 99441 non-null object
 2 customer_state 99441 non-null object
dtypes: object(3)
memory usage: 2.3+ MB
None
Missing data: False
--------------------------------------------------------------
order_items
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 112650 entries, 0 to 112649
Data columns (total 3 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 order_id 112650 non-null object 
 1 product_id 112650 non-null object 
 2 price 112650 non-null float64
dtypes: float64(1), object(2)
memory usage: 2.6+ MB
None
Missing data: False
--------------------------------------------------------------
order_payments
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99440 entries, 0 to 99439
Data columns (total 2 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 order_id 99440 non-null object 
 1 payment_value 99440 non-null float64
dtypes: float64(1), object(1)
memory usage: 1.5+ MB
None
Missing data: False
--------------------------------------------------------------
orders
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99441 entries, 0 to 99440
Data columns (total 2 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 order_id 99441 non-null object
 1 customer_id 99441 non-null object
dtypes: object(2)
memory usage: 1.5+ MB
None
Missing data: False
--------------------------------------------------------------
order_reviews
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 2 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 order_id 100000 non-null object
 1 review_score 100000 non-null int64 
dtypes: int64(1), object(1)
memory usage: 1.5+ MB
None
Missing data: False
--------------------------------------------------------------
product
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32951 entries, 0 to 32950
Data columns (total 9 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 product_id 32951 non-null object 
 1 product_category_name 32341 non-null object 
 2 product_name_lenght 32341 non-null float64
 3 product_description_lenght 32341 non-null float64
 4 product_photos_qty 32341 non-null float64
 5 product_weight_g 32949 non-null float64
 6 product_length_cm 32949 non-null float64
 7 product_height_cm 32949 non-null float64
 8 product_width_cm 32949 non-null float64
dtypes: float64(7), object(2)
memory usage: 2.3+ MB
None
Missing data: True
No. missing value: 
product_id 0
product_category_name 610
product_name_lenght 610
product_description_lenght 610
product_photos_qty 610
product_weight_g 2
product_length_cm 2
product_height_cm 2
product_width_cm 2
dtype: int64

--------------------------------------------------------------
product_name
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 71 entries, 0 to 70
Data columns (total 2 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 product_category_name 71 non-null object
 1 product_category_name_english 71 non-null object
dtypes: object(2)
memory usage: 1.2+ KB
None
Missing data: False
--------------------------------------------------------------
sellers
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3095 entries, 0 to 3094
Data columns (total 4 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 seller_id 3095 non-null object
 1 seller_zip_code_prefix 3095 non-null int64 
 2 seller_city 3095 non-null object
 3 seller_state 3095 non-null object
dtypes: int64(1), object(3)
memory usage: 96.8+ KB
None
Missing data: False
--------------------------------------------------------------

####### 1 customer can be in multiple states ==> drop state feature

In [0]:
# Check variable consistency
customers = customers[['customer_id',
                       'customer_unique_id',
                       'customer_state']]

customer = customers.groupby('customer_unique_id')['customer_state'].count().reset_index()
print(customer.loc[customer.customer_state==1,:]['customer_unique_id'].nunique())
print(customers['customer_unique_id'].nunique())

93099
96096

In [0]:
# Select required parameters
customers = customers[['customer_id',
                       'customer_unique_id']]


orders = orders[['order_id',
                 'customer_id']]

order_items = order_items[['order_id',
                           'product_id',
                           'price']]

order_payments = order_payments[['order_id',
                                 'payment_value']]\
                              .groupby('order_id')['payment_value']\
                              .sum()\
                              .reset_index()

order_reviews = order_reviews[['order_id',
                               'review_score']]

products = product[['product_id',
                    'product_category_name']]

# merge into one dataset
dfList = [orders,order_items, order_payments, order_reviews]

df1 = reduce(lambda left, 
                      right: pd.merge(left, 
                                     right, 
                                             on=['order_id'],
                                             how='inner'),
                dfList )

df1.drop_duplicates(keep='first',inplace=True)

df2 = df1.merge(customers,
                how="inner",
                left_on="customer_id",
                right_on="customer_id")

df3 = df2.merge(product,
                how="inner",
                left_on="product_id",
                right_on="product_id")

df4 = df3.merge(product_name,
                how="inner",
                left_on="product_category_name",
                right_on="product_category_name")

olist = df4[['order_id', 'customer_id', 'product_id', 'payment_value','price',
             'review_score', 'customer_unique_id', 
             'product_category_name_english']]

olist.drop_duplicates(keep='first',
                      inplace=True)

##### Split data into 2 datasets: 1) customers with more than 1 order; customers ordered first time

In [0]:
num_order = olist.groupby('customer_unique_id')['order_id']\
                .count()\
                .reset_index()

repeatList = num_order.loc[num_order.order_id>=2,:]['customer_unique_id'].unique()
firsttimeList = num_order.loc[num_order.order_id==1,:]['customer_unique_id'].unique()

repeat_olist = olist[olist['customer_unique_id'].isin(repeatList)]

firstime_olist =  olist[olist['customer_unique_id'].isin(firsttimeList)]

print(repeat_olist.customer_unique_id.nunique())
print(repeat_olist.product_id.nunique())
repeat_olist.head(3)

<command-3409070480001118>:56: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

In [0]:
product_price = repeat_olist[['product_id',
                             'price']]

product_price = product_price.groupby('product_id')['price']\
                            .mean()\
                            .reset_index()

col         = 'price'
conditions  = [ product_price[col] > 120, 
               (product_price[col] <= 120) & (product_price[col]> 65),
               (product_price[col] <= 65) & (product_price[col]> 35),
                product_price[col] <= 35 ]

choices     = [ "very_high",
                "high", 
               'medium',
               'low' ]
    
product_price["price"] = np.select(conditions, 
                                  choices, 
                                  default=np.nan)

dummies_price = pd.get_dummies(product_price['price'])


## Rating level
product_review = repeat_olist[['product_id',
                             'review_score']]
product_review.drop_duplicates(keep='first',inplace=True)
product_review = product_review.groupby('product_id')['review_score']\
                            .mean()\
                            .reset_index()

col         = 'review_score'
conditions  = [ product_review[col] > 2, 
                product_review[col] <= 2]

choices     = [ "like",
                "dislike" ]
    
product_review["review_score"] = np.select(conditions, 
                                  choices, 
                                  default=np.nan)

dummies_review = pd.get_dummies(product_review['review_score'])

product_review = pd.merge(
    left=product_review,
    right=dummies_review,
    left_index=True,
    right_index=True,
)
## product category
product_cat = repeat_olist[['product_id',
                             'product_category_name_english']]
product_cat.drop_duplicates(keep='first',inplace=True)

dummies_cat = pd.get_dummies(product_cat['product_category_name_english'])

product_cat = pd.merge(
    left=product_cat,
    right=dummies_cat,
    left_index=True,
    right_index=True,
)

product_features_list = [product_cat, product_review, product_price]

product_features = reduce(lambda left, 
                                  right: pd.merge(left, 
                                                  right, 
                                                  left_on = 'product_id', 
                                                  right_on='product_id',
                                                  how='inner'),
                            product_features_list )

product_features.product_id.nunique()

Out[129]: 7843

###### Create categorical variable for payment level

In [0]:
customer_pay = repeat_olist[['customer_unique_id',
                             'payment_value']]

customer_pay = customer_pay.groupby('customer_unique_id')['payment_value']\
                            .sum()\
                            .reset_index()
customer_pay.describe()

Out[111]:

payment_value 
 
 
 
 
 count 
 5699.00 
 
 
 mean 
 454.67 
 
 
 std 
 577.04 
 
 
 min 
 34.97 
 
 
 25% 
 186.85 
 
 
 50% 
 309.10 
 
 
 75% 
 510.00 
 
 
 max 
 15978.65

In [0]:
# CUSTOMER FEATURE
customer_pay = repeat_olist[['customer_unique_id', 'payment_value']]

customer_pay = customer_pay.groupby('customer_unique_id')['payment_value']\
                            .sum()\
                            .reset_index()

col         = 'payment_value'
conditions  = [ customer_pay[col] > 510, 
               (customer_pay[col] <= 510) & (customer_pay[col]> 309),
               (customer_pay[col] <= 309) & (customer_pay[col]> 187),
                customer_pay[col] <= 187 ]

choices     = [ "very_high",
                "high", 
               'medium',
               'low' ]
    
customer_pay["pay_level"] = np.select(conditions, 
                                  choices, 
                                  default=np.nan)

dummies_pay = pd.get_dummies(customer_pay["pay_level"])
customer_features = pd.merge(
    left=customer_pay,
    right=dummies_pay,
    left_index=True,
    right_index=True,
    how = "inner"
)

customer_features 


Out[112]:

customer_unique_id 
 payment_value 
 pay_level 
 high 
 low 
 medium 
 very_high 
 
 
 
 
 0 
 00053a61a98854899e70ed204dd4bafe 
 838.36 
 very_high 
 0 
 0 
 0 
 1 
 
 
 1 
 000bfa1d2f1a41876493be685390d6d3 
 93.70 
 low 
 0 
 1 
 0 
 0 
 
 
 2 
 000de6019bb59f34c099a907c151d855 
 514.88 
 very_high 
 0 
 0 
 0 
 1 
 
 
 3 
 000fbf0473c10fc1ab6f8d2d286ce20c 
 724.76 
 very_high 
 0 
 0 
 0 
 1 
 
 
 4 
 001926cef41060fae572e2e7b30bd2a4 
 182.42 
 low 
 0 
 1 
 0 
 0 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 5694 
 ffb973f2bb1c0cb807a99341a9b20dcd 
 218.04 
 medium 
 0 
 0 
 1 
 0 
 
 
 5695 
 ffd6f65402f2bc47238ecd2bdc93e0d4 
 166.92 
 low 
 0 
 1 
 0 
 0 
 
 
 5696 
 ffe254cc039740e17dd15a5305035928 
 80.12 
 low 
 0 
 1 
 0 
 0 
 
 
 5697 
 fff7219c86179ca6441b8f37823ba3d3 
 531.60 
 very_high 
 0 
 0 
 0 
 1 
 
 
 5698 
 fffcf5a5ff07b0908bd4e2dbc735a684 
 4134.84 
 very_high 
 0 
 0 
 0 
 1 
 
 
 
 5699 rows × 7 columns

## Create customer-product interaction dataset

In [0]:
interaction = repeat_olist[['customer_unique_id','product_id','review_score']]
interaction.drop_duplicates(keep='first',inplace=True)

# Normalization 
col         = 'review_score'
conditions  = [ interaction[col] >= 3, 
                interaction[col] <= 2]

choices     = [ 1,0 ]
    
interaction["review_score"] = np.select(conditions, 
                                  choices, 
                                  default=np.nan)

interaction = pd.pivot_table(interaction,
                                       index='customer_unique_id',
                                       columns='product_id',
                                       values='review_score')

interaction = interaction.fillna(0)
interaction

<command-829222027270942>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

7843
5699
<command-829222027270942>:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

Out[128]:

product_id 
 0011c512eb256aa0dbbb544d8dffcf6e 
 001b72dfd63e9833e8c02742adf472e3 
 00210e41887c2a8ef9f791ebc780cc36 
 002159fe700ed3521f46cfcf6e941c76 
 00250175f79f584c14ab5cecd80553cd 
 002959d7a0b0990fe2d69988affcbc80 
 0042f1a9a7e0edd1400c6cd0fda065f8 
 005030ef108f58b46b78116f754d8d38 
 0060b415594c5e1200324ef1a18493c4 
 007c63ae4b346920756b5adcad8095de 
 008cff0e5792219fae03e570f980b330 
 00905d58c87afcbce21420b3712cacaa 
 00989337a1916a0055eedd1fdb35eb53 
 009af1277432f1a05742df69cdf72d1e 
 009c09f439988bc06a93d6b8186dce73 
 00ba6d766f0b1d7b78a5ce3e1e033263 
 00baba5b58e274d0332a0c8a0a66f877 
 00bc6e6d4ceb98ec7ed058b0a243a8b9 
 00d2fa6f2a87633084c8e0400d41a65a 
 00de7f393d962717eeeb2d7131a40dba 
 00f42e56821b1779fbf397fe72639054 
 00faa46f36261af8bbf3a4d37fa4841b 
 010a3a47c14f1295796c08419f32cef6 
 010c988805cc0a13b9ba455ffc6c8510 
 0110573bc9195aa810a4384f189f48f5 
 0111ab6fb41da433e0f17d3f4ec2c8f5 
 011377a7487fef47fc9e73fa5f7322a6 
 011bb8a6af5178b33871a83c4f297d32 
 011c2759ca1a29c74ecd8bfa48d0ac14 
 0129d1e9b29d3fe6833cc922374cd252 
 01365901d8f2247976a7e5d4c98c52c0 
 013e6676e0e3529e5909ff54370daddf 
 013ee64977aaa6b2b25475095162e0e9 
 01422266d7a3131403364787ef9dab11 
 014a8a503291921f7b004a5215bb3c36 
 014d94f219fbff1166b9cf700eee36b2 
 0152f69b6cf919bcdaf117aa8c43e5a2 
 015e04445dedbd5da301ef29cbb03f83 
 0160785b697a5ea87d52949bd097ce05 
 0164201c7c8b81dc5779e015e2d7be59 
 016711f78a6a87696645db0a6a834826 
 0168e1b28d8e55a515928cf656eff0a4 
 016cae136d358dcdacbd7ac9f1864c09 
 017692475c1c954ff597feda05131d73 
 0185f302dc17abf603edfe7929a0120a 
 019003324f0a201dd2c8962beaf94b6d 
 0193fc18d9a6e9b9b0b3a41768fefa12 
 01a184b7d8422cd95e9cf2a8cff32b5e 
 01b0238705b6ae8e35c6fea837e6ae4a 
 01b660ebc1a0c293ccf9b117fa6dd8bb 
 01bc2a3c12d6e588aecb54ffad194c13 
 01c2e91674406ebaca6a1bbf7f61c3f0 
 01cf7c4cffff8db0a1cbe612bd2d50a4 
 01cfc3d9c29504c2d370933e53f002b4 
 01d15932271068f9fd1f369b8449cac1 
 01d40fca05c4227b987ee069be837b49 
 01d4157fd9738ea81038316ae4cfc192 
 01e20e6604216c8adb31d463214ba00c 
 01ef0716b68c8493434ad32430c24e18 
 01fc56750f0d3444c4a1746ecf19dee0 
 01ff1ff8aa5dec93e9938b989393a4ca 
 02090f97a28b3d10d19a09f045f6df34 
 020a80cb704bf65f38761fcedf2af192 
 0210b75f6f4de09dfc17a66803290f8a 
 023a60ac6b3484afe23d788ce2444df0 
 02475368dfb38934fe55f574024fe1d7 
 025dd9fac2544d8e7e3451ec87bc6511 
 02623b0e4e6b951aefb23575de1f3886 
 027325f946f1b3d8f94c3496e9a59a10 
 027cdd14a677a5834bc67a9789db5021 
 0288f8dd74b931b4ec7a468fdd6ed040 
 028b3574d7619f191a7345161ae590e4 
 0294e314a033317e28ecc40aee9025e8 
 02a0c276d5a252215b48269dea73a6e7 
 02a99f266fc960423c1186ecbd627804 
 02ed3b595447e948efc3eac897e4df0e 
 030729544fc3eb6a40981f877e836450 
 0320a1be5c5224f64bfbffa583cf03d6 
 032c32a02f67b0fad495803ca810689e 
 0333795efd58e3c33c5850b92721c3e4 
 033ccb3016d3b24bc724629b8df41f94 
 03552ec45033c8658713c541f6af9f05 
 03566b85189259c49476f004ad2afd08 
 035df2b15f358d231e00af9e62488cf4 
 03624ffc0958f7ea385b6d4e088532b0 
 0364c36f8e845e4d309c0a3accc04b1c 
 036734b5a58d5d4f46b0616ddc047ced 
 0369a47f7ad96df46ad8ed76767de8bd 
 036bcd084feae22f3a997f5080ec30df 
 036ecb2f1816e95d3fa658207266ecf5 
 03a20f79e4c056b48ce29b3e30beb0fb 
 03b58043df5d7424df7eac2be2511c51 
 03ba2b6c24374d16022585b6b1b385e1 
 03bb06cda40712fb8473f7962fb7d198 
 03d4233b9e3382adaed9e5c58626f1dc 
 03d817e5e392e78674ed0bd8195f9159 
 03e606af3a694d55bf9abce7f5b07c42 
 03e931f387c2dd5b006aecdb12515b2e 
 03f02ee5e8fd233d41dcfe8ad911cf7e 
 040fe1cdb263eb2c9b1322875b0afcb7 
 0424d4d1508370eb771126734ec9740e 
 0432203d03868bfe5fdbb86fb2148474 
 0437850bd55b9b2b9cf104b59a611666 
 0449db5eede617c5fd413071d582f038 
 044f05bc9de36e8a693a83e4bc79dd0d 
 04566e1a1afa83470b25c2642706fc32 
 045e41f597e72ebfe5e9de50788fbf03 
 046eee903d62294ffad4e38ae6aa730e 
 04869307f7e7dc5b07f1d83406ade1e5 
 048bb098a0e194ddc3d0287b954bc9d8 
 049ac5dce8536884a652ce73c58022ab 
 04a4e9d8c0dc6b2b4b8e24ea78a8f318 
 04a67e69edfb208f784da30294f69c5b 
 04af9f3af5c6afc4eece909c25330934

In [0]:
item_features.to_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/item_features_data.csv')
customer_features.to_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/customer_features_data.csv')
interaction.to_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/interaction_data.csv')
firsttime_olist.to_csv('/dbfs//FileStore/shared_uploads/phuong.le@man-es.com/firsttime_data.csv')